In [6]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import numpy as np
from tqdm import tqdm
import csv
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import time
from urllib.parse import urljoin
import pickle
import re

In [7]:
def selenium_set():

    global driver
    
    # chrome path setting
    driver_path = "/workspace/chromedriver-linux64/chromedriver"
    chrome_path = "/workspace/chrome-linux64/chrome"
    
    chrome_options = webdriver.ChromeOptions()
    
    chrome_options.binary_location = chrome_path
    chrome_options.add_argument("--headless")
    chrome_options.add_argument("--no-sandbox")
    chrome_options.add_argument("--disable-dev-shm-usage")
    
    service = Service(executable_path=driver_path)
    
    driver = webdriver.Chrome(service=service, options=chrome_options)

In [8]:
#topic별 url 리스트 반환
def make_topic_urllist(data, base_url):
    urllist=[]
    topic_txt_lnb=pd.read_csv(data, encoding='utf-8')
    for row in topic_txt_lnb.iloc[:,1]:
        url = base_url + str(row)
        urllist.append(url) 
    return urllist

In [9]:
def scroll_click_extract(url):

    """
    - 페이지 바닥까지 스크롤하면서 '기사 더보기' 버튼을 반복 클릭
    - 반복이 끝나면 현재 페이지의 모든 기사 링크를 수집하여 DataFrame 반환
    """
    
    global driver
    driver.get(url)

    try:
        response = requests.get(url)
        response.raise_for_status()  # 문제가 발생하면 예외 발생
        html = response.text
    except requests.exceptions.RequestException as e:
        print(f"웹 페이지 요청 오류: {e}")
        exit()

    
    # XPath로 '기사 더보기' 버튼 찾기
    refresh_btn = driver.find_element(By.XPATH, '//a[contains(@class, "_CONTENT_LIST_LOAD_MORE_BUTTON")]')

    count = 0
    
    while True: ############ 클릭 끝까지로 바꾸기 ############
        count += 1
        print(f"[LOOP] {count} 번째 반복 중...")
        
        try:
            # 페이지 끝까지 스크롤하기
            body = driver.find_element(By.CSS_SELECTOR, 'body')
            for _ in range(10):  # 10번 정도 END 키 누르기
                body.send_keys(Keys.END)

            # 클릭
            # driver.execute_script("arguments[0].click();", refresh_btn)
            # time.sleep(1)  # 새 기사 로딩 대기

            # 최대 5초간 '기사 더보기' 버튼이 클릭 가능해질 때까지 기다림
            button = WebDriverWait(driver, 3).until(
                EC.element_to_be_clickable((By.XPATH, '//a[contains(@class, "_CONTENT_LIST_LOAD_MORE_BUTTON")]'))
            )
            button.click()
            print(f" → 버튼 클릭 성공 ({count}회)")
                        
        except Exception as e:
            print("기사 더보기 버튼 클릭 실패:", e)
            break

    """
    --- 불러온 HTMl에서 기사 링크 모두 추출 ---
    """

    # 버튼 클릭으로 새로 로드된 기사들은 Selenium이 로드한 DOM에만 존재하므로 request에는 안잡힘.
    html = driver.page_source
    soup = BeautifulSoup(html, 'html.parser')

    # 뉴스 기사 링크 추출

    news_tag = soup.select('a.sa_text_title._NLOG_IMPRESSION')

    article_url_list = []

    for i in news_tag:
        href = i.get('href')
        full_url = urljoin(url, href)
        
        if href:
            article_url_list.append(full_url)

        else:
            break
    
    print("----url추출 및 list에 보냄----")

    return article_url_list

In [10]:
def crawl_with_selenium():

    global driver
    global data, base_url
    
    # __main__
    topic_urls = make_topic_urllist(data, base_url)
    
    article_url = [] # 모든 단일기사 url 저장 리스트

    for u in tqdm(range(len(topic_urls))):
        
        print("--토픽별 단일 기사 url 크롤링 시작---")
        article_url.append(scroll_click_extract(topic_urls[u]))
        
    return article_url

In [11]:
### Test 실행 cell

driver = None
data = "../crawling_base_data/naver_topicset.csv"
base_url = "https://news.naver.com/breakingnews/section"
article_topic_df=[]
article_single_url_set=[]


def exec_code():
    selenium_set() 
    global article_topic_df
    global article_single_url_set
    
    article_topic_df=make_topic_urllist(data, base_url)
    article_single_url_set=crawl_with_selenium()

    return article_topic_df, article_single_url_set

In [9]:
exec_code()

  0%|          | 0/48 [00:00<?, ?it/s]

--토픽별 단일 기사 url 크롤링 시작---
[LOOP] 1 번째 반복 중...
 → 버튼 클릭 성공 (1회)
[LOOP] 2 번째 반복 중...
 → 버튼 클릭 성공 (2회)
[LOOP] 3 번째 반복 중...
 → 버튼 클릭 성공 (3회)
[LOOP] 4 번째 반복 중...
 → 버튼 클릭 성공 (4회)
[LOOP] 5 번째 반복 중...
 → 버튼 클릭 성공 (5회)
[LOOP] 6 번째 반복 중...
 → 버튼 클릭 성공 (6회)
[LOOP] 7 번째 반복 중...
 → 버튼 클릭 성공 (7회)
[LOOP] 8 번째 반복 중...
 → 버튼 클릭 성공 (8회)
[LOOP] 9 번째 반복 중...
 → 버튼 클릭 성공 (9회)
[LOOP] 10 번째 반복 중...
 → 버튼 클릭 성공 (10회)
[LOOP] 11 번째 반복 중...
 → 버튼 클릭 성공 (11회)
[LOOP] 12 번째 반복 중...
 → 버튼 클릭 성공 (12회)
[LOOP] 13 번째 반복 중...
 → 버튼 클릭 성공 (13회)
[LOOP] 14 번째 반복 중...
 → 버튼 클릭 성공 (14회)
[LOOP] 15 번째 반복 중...
 → 버튼 클릭 성공 (15회)
[LOOP] 16 번째 반복 중...
 → 버튼 클릭 성공 (16회)
[LOOP] 17 번째 반복 중...
 → 버튼 클릭 성공 (17회)
[LOOP] 18 번째 반복 중...
 → 버튼 클릭 성공 (18회)
[LOOP] 19 번째 반복 중...
 → 버튼 클릭 성공 (19회)
[LOOP] 20 번째 반복 중...
 → 버튼 클릭 성공 (20회)
[LOOP] 21 번째 반복 중...
 → 버튼 클릭 성공 (21회)
[LOOP] 22 번째 반복 중...
 → 버튼 클릭 성공 (22회)
[LOOP] 23 번째 반복 중...
 → 버튼 클릭 성공 (23회)
[LOOP] 24 번째 반복 중...
 → 버튼 클릭 성공 (24회)
[LOOP] 25 번째 반복 중...
 → 버튼 클릭 성공 (25회)
[LOOP] 26 번째 반복 중

  2%|▏         | 1/48 [00:55<43:31, 55.56s/it]

----url추출 및 list에 보냄----
--토픽별 단일 기사 url 크롤링 시작---
[LOOP] 1 번째 반복 중...
 → 버튼 클릭 성공 (1회)
[LOOP] 2 번째 반복 중...
 → 버튼 클릭 성공 (2회)
[LOOP] 3 번째 반복 중...
 → 버튼 클릭 성공 (3회)
[LOOP] 4 번째 반복 중...
 → 버튼 클릭 성공 (4회)
[LOOP] 5 번째 반복 중...
 → 버튼 클릭 성공 (5회)
[LOOP] 6 번째 반복 중...
 → 버튼 클릭 성공 (6회)
[LOOP] 7 번째 반복 중...
 → 버튼 클릭 성공 (7회)
[LOOP] 8 번째 반복 중...
 → 버튼 클릭 성공 (8회)
[LOOP] 9 번째 반복 중...
 → 버튼 클릭 성공 (9회)
[LOOP] 10 번째 반복 중...
 → 버튼 클릭 성공 (10회)
[LOOP] 11 번째 반복 중...
 → 버튼 클릭 성공 (11회)
[LOOP] 12 번째 반복 중...
 → 버튼 클릭 성공 (12회)
[LOOP] 13 번째 반복 중...
 → 버튼 클릭 성공 (13회)
[LOOP] 14 번째 반복 중...
 → 버튼 클릭 성공 (14회)
[LOOP] 15 번째 반복 중...
 → 버튼 클릭 성공 (15회)
[LOOP] 16 번째 반복 중...
 → 버튼 클릭 성공 (16회)
[LOOP] 17 번째 반복 중...
 → 버튼 클릭 성공 (17회)
[LOOP] 18 번째 반복 중...
 → 버튼 클릭 성공 (18회)
[LOOP] 19 번째 반복 중...
 → 버튼 클릭 성공 (19회)
[LOOP] 20 번째 반복 중...
 → 버튼 클릭 성공 (20회)
[LOOP] 21 번째 반복 중...
 → 버튼 클릭 성공 (21회)
[LOOP] 22 번째 반복 중...
 → 버튼 클릭 성공 (22회)
[LOOP] 23 번째 반복 중...
 → 버튼 클릭 성공 (23회)
[LOOP] 24 번째 반복 중...
 → 버튼 클릭 성공 (24회)
[LOOP] 25 번째 반복 중...
 → 버튼 클릭 성

  4%|▍         | 2/48 [08:26<3:40:58, 288.23s/it]

...

 98%|█████████▊| 47/48 [1:39:40<00:35, 35.01s/it]

----url추출 및 list에 보냄----
--토픽별 단일 기사 url 크롤링 시작---
[LOOP] 1 번째 반복 중...
 → 버튼 클릭 성공 (1회)
[LOOP] 2 번째 반복 중...
 → 버튼 클릭 성공 (2회)
[LOOP] 3 번째 반복 중...
 → 버튼 클릭 성공 (3회)
[LOOP] 4 번째 반복 중...
 → 버튼 클릭 성공 (4회)
[LOOP] 5 번째 반복 중...
 → 버튼 클릭 성공 (5회)
[LOOP] 6 번째 반복 중...
 → 버튼 클릭 성공 (6회)
[LOOP] 7 번째 반복 중...
 → 버튼 클릭 성공 (7회)
[LOOP] 8 번째 반복 중...
 → 버튼 클릭 성공 (8회)
[LOOP] 9 번째 반복 중...
 → 버튼 클릭 성공 (9회)
[LOOP] 10 번째 반복 중...
 → 버튼 클릭 성공 (10회)
[LOOP] 11 번째 반복 중...
 → 버튼 클릭 성공 (11회)
[LOOP] 12 번째 반복 중...
 → 버튼 클릭 성공 (12회)
[LOOP] 13 번째 반복 중...
 → 버튼 클릭 성공 (13회)
[LOOP] 14 번째 반복 중...
 → 버튼 클릭 성공 (14회)
[LOOP] 15 번째 반복 중...
 → 버튼 클릭 성공 (15회)
[LOOP] 16 번째 반복 중...
 → 버튼 클릭 성공 (16회)
[LOOP] 17 번째 반복 중...
 → 버튼 클릭 성공 (17회)
[LOOP] 18 번째 반복 중...
 → 버튼 클릭 성공 (18회)
[LOOP] 19 번째 반복 중...
 → 버튼 클릭 성공 (19회)
[LOOP] 20 번째 반복 중...
 → 버튼 클릭 성공 (20회)
[LOOP] 21 번째 반복 중...
 → 버튼 클릭 성공 (21회)
[LOOP] 22 번째 반복 중...
 → 버튼 클릭 성공 (22회)
[LOOP] 23 번째 반복 중...
 → 버튼 클릭 성공 (23회)
[LOOP] 24 번째 반복 중...
 → 버튼 클릭 성공 (24회)
[LOOP] 25 번째 반복 중...
 → 버튼 클릭 성

100%|██████████| 48/48 [1:42:33<00:00, 128.19s/it]

----url추출 및 list에 보냄----


(['https://news.naver.com/breakingnews/section/100/264',
  'https://news.naver.com/breakingnews/section/100/265',
  'https://news.naver.com/breakingnews/section/100/268',
  'https://news.naver.com/breakingnews/section/100/266',
  'https://news.naver.com/breakingnews/section/100/267',
  'https://news.naver.com/breakingnews/section/100/269',
  'https://news.naver.com/breakingnews/section/101/259',
  'https://news.naver.com/breakingnews/section/101/258',
  'https://news.naver.com/breakingnews/section/101/261',
  'https://news.naver.com/breakingnews/section/101/771',
  'https://news.naver.com/breakingnews/section/101/260',
  'https://news.naver.com/breakingnews/section/101/262',
  'https://news.naver.com/breakingnews/section/101/310',
  'https://news.naver.com/breakingnews/section/101/263',
  'https://news.naver.com/breakingnews/section/102/249',
  'https://news.naver.com/breakingnews/section/102/250',
  'https://news.naver.com/breakingnews/section/102/251',
  'https://news.naver.com/break

In [10]:
# article_single_url_set = 단일 기사의 링크를 토픽별 이중리스트 형태로 저장
article_single_url_set 

[['https://n.news.naver.com/mnews/article/422/0000768904',
  'https://n.news.naver.com/mnews/article/018/0006085800',
  'https://n.news.naver.com/mnews/article/008/0005233575',
  'https://n.news.naver.com/mnews/article/421/0008419432',
  'https://n.news.naver.com/mnews/article/003/0013412438',
  'https://n.news.naver.com/mnews/article/001/0015556892',
  'https://n.news.naver.com/mnews/article/421/0008419419',
  'https://n.news.naver.com/mnews/article/079/0004054143',
  'https://n.news.naver.com/mnews/article/469/0000880641',
  'https://n.news.naver.com/mnews/article/020/0003653211',
  'https://n.news.naver.com/mnews/article/020/0003653202',
  'https://n.news.naver.com/mnews/article/020/0003653170',
  'https://n.news.naver.com/mnews/article/001/0015556867',
  'https://n.news.naver.com/mnews/article/005/0001794798',
  'https://n.news.naver.com/mnews/article/366/0001099125',
  'https://n.news.naver.com/mnews/article/001/0015556832',
  'https://n.news.naver.com/mnews/article/008/0005233552

In [21]:
# article_single_url_set을 피클 백업파일로 저장
with open('../crawling_base_data/url_list_backup.pkl', 'wb') as f:
    pickle.dump(article_single_url_set, f)

In [17]:
# 크롤링한 기사의 갯수
article_counts=0

for i in tqdm(range(len(article_single_url_set))):
    article_counts=article_counts+len(article_single_url_set[i])
    print('total:', article_counts,"  |  ", f'topic{i}의 기사 갯수:', len(article_single_url_set[i]))

100%|██████████| 48/48 [00:00<00:00, 14782.77it/s]

total: 1529   |   topic0의 기사 갯수: 1529
total: 10589   |   topic1의 기사 갯수: 9060
total: 11133   |   topic2의 기사 갯수: 544
total: 12485   |   topic3의 기사 갯수: 1352
total: 14589   |   topic4의 기사 갯수: 2104
total: 14625   |   topic5의 기사 갯수: 36
total: 17399   |   topic6의 기사 갯수: 2774
total: 22571   |   topic7의 기사 갯수: 5172
total: 31233   |   topic8의 기사 갯수: 8662
total: 32565   |   topic9의 기사 갯수: 1332
total: 34606   |   topic10의 기사 갯수: 2041
total: 35665   |   topic11의 기사 갯수: 1059
total: 38897   |   topic12의 기사 갯수: 3232
total: 38933   |   topic13의 기사 갯수: 36
total: 44751   |   topic14의 기사 갯수: 5818
total: 46376   |   topic15의 기사 갯수: 1625
total: 46956   |   topic16의 기사 갯수: 580
total: 47192   |   topic17의 기사 갯수: 236
total: 47799   |   topic18의 기사 갯수: 607
total: 48606   |   topic19의 기사 갯수: 807
total: 49615   |   topic20의 기사 갯수: 1009
total: 49651   |   topic21의 기사 갯수: 36
total: 50884   |   topic22의 기사 갯수: 1233
total: 50920   |   topic23의 기사 갯수: 36
total: 52023   |   topic24의 기사 갯수: 1103
total: 52848   |   topic

In [65]:
print(article_single_url_set[1][7060])

https://n.news.naver.com/mnews/article/468/0001166870


In [29]:
# 컬럼을 토픽명으로 달아준 데이터프레임으로 만든다음 피클로 저장하는 셀

col_temp = pd.read_csv(data)
name_list = col_temp['name'].tolist()

article_final_url_df_to_pickle = []

for i in range(len(article_single_url_set)):
    temp_df = pd.DataFrame(article_single_url_set[i], columns=[name_list[i]])
    article_final_url_df_to_pickle.append(temp_df)


with open('../crawling_base_data/final_url_df_backup_.pkl', 'wb') as f:
    pickle.dump(article_final_url_df_to_pickle, f)   

In [20]:

# 피클 파일 읽기
with open("../crawling_base_data/final_url_df_backup_.pkl", "rb") as f:  # rb = read binary
     article_final_url_df_to_pickle= pickle.load(f)

print(article_final_url_df_to_pickle)  # 내용 출력


[                                                   대통령실
0     https://n.news.naver.com/mnews/article/422/000...
1     https://n.news.naver.com/mnews/article/018/000...
2     https://n.news.naver.com/mnews/article/008/000...
3     https://n.news.naver.com/mnews/article/421/000...
4     https://n.news.naver.com/mnews/article/003/001...
...                                                 ...
1524  https://n.news.naver.com/mnews/article/021/000...
1525  https://n.news.naver.com/mnews/article/421/000...
1526  https://n.news.naver.com/mnews/article/421/000...
1527  https://n.news.naver.com/mnews/article/018/000...
1528  https://n.news.naver.com/mnews/article/032/000...

[1529 rows x 1 columns],                                                   국회/정당
0     https://n.news.naver.com/mnews/article/021/000...
1     https://n.news.naver.com/mnews/article/003/001...
2     https://n.news.naver.com/mnews/article/421/000...
3     https://n.news.naver.com/mnews/article/032/000...
4     https://n.news.

In [25]:
# 필요없는 것 같은데 일단 나두는 셀

what_is_this = []

for i in range(len(name_list)):

    row = [name_list[i]] + article_single_url_set[i]
    what_is_this.append(row)

what_is_this_df= pd.DataFrame(what_is_this)

In [61]:
#copyright 추가해서 잘 걸러지는지 확인하는 셀
# 기사의 제목과 내용을 담을 리스트

# article_contents = []

# for i in tqdm(range(1)):

#     temp_df = pd.DataFrame(columns=["title", "content", "copyright"])

#     for j in tqdm(range(10)):
#          # copyright에서 걸러진 기사는 패스
#         contents = article_crawler(article_final_url_df_to_pickle[i].iloc[j, 0])
#         if contents is not None:
#             title, content, copyright = contents

#         else:
#             continue

#         row_df = pd.DataFrame([(title, content, copyright)], columns=["title", "content", "copyright"])
#         temp_df = pd.concat([temp_df, row_df], axis=0, ignore_index=True)
    
#     #기사 제목과 내용 저장 (데이터프레임을 담은 리스트)
#     article_contents.append(temp_df)

In [ ]:
#copyright 확인하는 셀
#제목, 날짜, 기사 내용 크롤

# def article_crawler(url):
#     try:
#         response = requests.get(url)
#         response.raise_for_status()  # 문제가 발생하면 예외 발생
#         html = response.text
        
#     except requests.exceptions.RequestException as e:
#         print(f"웹 페이지 요청 오류: {e}")
#         exit()
        
#     soup=BeautifulSoup(html,'html.parser')
    
#     # content 검색하여 AI, ...키워드로 삭제 저장 X
#     copyright=soup.find('p',{'class':'c_text'}).text.strip()
#     AI_ban=['AI', '인공', '학습', '크롤링', '상업', '수익']
            
#     for i in AI_ban:
#         if i in copyright:
#             return None
            
#     title = soup.find('title').text.strip() # title
#     content = soup.find("article",id='dic_area').text.strip() # content
#     check_copyright = copyright

#     #title = soup.find('title').get_text(strip=True)
    
#     #raw_content = soup.find("article", id='dic_area').get_text()
#     #content = re.sub(r'\s+', ' ', raw_content).strip()
    
#     return title, content, copyright

In [17]:
#제목, 날짜, 기사 내용 크롤
def article_crawler(url):
    html=None
    try:
        response = requests.get(url)
        response.raise_for_status()  # 문제가 발생하면 예외 발생
        html = response.text
        
    except requests.exceptions.RequestException as e:
        print(f"웹 페이지 요청 오류: {e}")
        pass
        
    if html is None:
        return None
        
    soup=BeautifulSoup(html,'html.parser')

    # copyright 태그가 있는지 체크후 넘겨주기
    c_tag = soup.find('p', {'class': 'c_text'})
    if not c_tag:
        return None
    copyright = c_tag.text.strip()
    
    # content 검색하여 AI, ...키워드로 삭제 저장 X
    #copyright=soup.find('p',{'class':'c_text'}).text.strip()
    
    AI_ban=['AI', '인공', '학습', '크롤링', '상업', '수익']
            
    for i in AI_ban:
        if i in copyright:
            return None

    # title 태그 체크
    t_tag = soup.find('title')
    if not t_tag:
        return None
    title = t_tag.text.strip()

    # content 태그 체크
    a_tag = soup.find("article", id='dic_area')
    if not a_tag:
        return None
    content = a_tag.text.strip()
            
    # title = soup.find('title').text.strip() # title
    
    # content = soup.find("article",id='dic_area').text.strip() # content

    #title = soup.find('title').get_text(strip=True)
    
    #raw_content = soup.find("article", id='dic_area').get_text()
    #content = re.sub(r'\s+', ' ', raw_content).strip()
    
    return title, content

In [18]:
article_crawler('https://n.news.naver.com/mnews/article/011/0004519073')

웹 페이지 요청 오류: 404 Client Error: Not Found for url: https://n.news.naver.com/mnews/article/011/0004519073


In [67]:
# 찐
# 기사의 제목과 내용을 담을 리스트
article_contents = []

# 진행바 1개만 사용: 전체 URL 수
'''
total = sum(len(df) for df in article_final_url_df_to_pickle)

with tqdm(total=total, desc="전체 URL 크롤링", ncols=0) as pbar:
    for i in range(len(article_final_url_df_to_pickle)):
        temp_df = pd.DataFrame(columns=["title", "content"])

        for j in range(len(article_final_url_df_to_pickle[i])):
            # copyright에서 걸러진 기사는 패스
            contents = article_crawler(article_final_url_df_to_pickle[i].iloc[j, 0])
            if contents is not None:
                title, content = contents
                row_df = pd.DataFrame([(title, content)], columns=["title", "content"])
                temp_df = pd.concat([temp_df, row_df], axis=0, ignore_index=True)
            else:
                continue
            # 한 URL 처리 끝날 때마다 1 증가
            pbar.update(1)

        #기사 제목과 내용 저장 (데이터프레임을 담은 리스트)
        article_contents.append(temp_df)
'''

전체 URL 크롤링:  87% 69587/79818 [5:06:06<45:00,  3.79it/s]   

웹 페이지 요청 오류: 404 Client Error: Not Found for url: https://n.news.naver.com/mnews/article/011/0004519073


UnboundLocalError: local variable 'html' referenced before assignment

In [23]:
# 찐
# 기사의 제목과 내용을 담을 리스트
article_contents = []

# 진행바 1개만 사용: 전체 URL 수
total = sum(len(df) for df in article_final_url_df_to_pickle)

with tqdm(total=total, desc="전체 URL 크롤링", ncols=0) as pbar:
    for i in range(len(article_final_url_df_to_pickle)):
        temp_df = pd.DataFrame(columns=["title", "content"])

        for j in range(len(article_final_url_df_to_pickle[i])):
            # copyright에서 걸러진 기사는 패스
            contents = article_crawler(article_final_url_df_to_pickle[i].iloc[j, 0])
            if contents is not None:
                title, content = contents
                row_df = pd.DataFrame([(title, content)], columns=["title", "content"])
                temp_df = pd.concat([temp_df, row_df], axis=0, ignore_index=True)
            else:
                continue
            pbar.update(1)
        article_contents.append(temp_df)
        with open(f'../crawling_base_data/backup_files/article_contents_backup_df_{i}.pkl', 'wb') as f:
            pickle.dump(article_contents[i], f) 
        print(f'saved : article_contents_backup_df_{i}.pkl')
        

전체 URL 크롤링:   1% 832/79818 [05:35<7:08:09,  3.07it/s] 

saved : article_contents_backup_df_0.pkl


전체 URL 크롤링:   6% 5187/79818 [43:04<6:29:34,  3.19it/s] 

saved : article_contents_backup_df_1.pkl


전체 URL 크롤링:   7% 5465/79818 [44:57<13:21:31,  1.55it/s]

...

saved : article_contents_backup_df_45.pkl


전체 URL 크롤링:  59% 46742/79818 [4:52:18<2:56:58,  3.11it/s]

saved : article_contents_backup_df_46.pkl


전체 URL 크롤링:  62% 49426/79818 [5:09:27<3:10:17,  2.66it/s] 

saved : article_contents_backup_df_47.pkl


In [45]:
print(article_contents[0])

                                           title  \
0               휴가 다녀온 이 대통령…한미회담 준비·특별사면 결단 어떻게   
1                     케데헌 돌풍, 뭣이 중할까?[김유성의 통캐스트]   
2  휴가 복귀하는 이 대통령…조국 사면·대주주 기준·한미 정상회담 등 현안 해법 주목   
3                    휴가 마친 李대통령, 한미·한일 정상회담 준비는?   
4        ①한미회담 ②조국 사면 ③양도세... 휴가 마친 이 대통령의 당면 과제   

                                             content  \
0  [앵커]이재명 대통령이 거제 저도에서 보낸 첫 여름 휴가를 마치고 복귀했습니다.당장...   
1  넷플릭스 통해 K콘텐츠 전 세계적 관심 받아한류·K콘텐츠가 하나의 문화 현상으로 정...   
2  '조국 사면' 최종 결심 여부 주목…12일 국무회의서 확정대주주 기준 하향 여부…개...   
3  한미 정상회담 25일 전망…방일 먼저 할 가능성도李대통령, 닷새간 저도 휴가 마치고...   
4  이재명 대통령이 2024년 11월 더불어민주당 대표 시절 국회에서 열린 본회의에서 ...   

                                           copyright  
0  Copyright ⓒ 연합뉴스TV. All rights reserved. 무단 전재...  
1  Copyright ⓒ 이데일리. All rights reserved. 무단 전재 및...  
2  Copyright ⓒ 뉴시스. All rights reserved. 무단 전재 및 ...  
3  Copyright ⓒ 노컷뉴스. All rights reserved. 무단 전재 및...  
4  Copyright ⓒ 한국일보. All rights reserved. 무단 전재 및...  
